In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        os.path.join(dirname, filename)

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/resnet18/ResNet18_model.pth
/kaggle/input/miniimagenet/train/n02457408/n0245740800001088.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000155.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000191.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000181.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000709.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000043.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000977.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800001089.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000994.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000405.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000993.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000913.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000197.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245740800000173.jpg
/kaggle/input/miniimagenet/train/n02457408/n0245

In [ ]:
!pip install torch torchvision

In [2]:
import warnings
warnings.filterwarnings("ignore") 
import os
import shutil
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split

In [3]:
import torch
import time
from tqdm import tqdm
import torchvision
from torch import nn, optim
from torch.utils.data import DataLoader
from torchvision import transforms, datasets
import optuna

from torchvision import models
from torchvision.transforms import transforms
from torchvision.models import resnet18, vgg16
from torch.nn import Linear, CrossEntropyLoss

import tensorflow as tf
# from tensorflow.keras.applications import ResNet50, ResNet50V2, ResNet152V2, VGG19
# from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint

In [4]:
train_path = '/kaggle/input/miniimagenet/train/'
output_path = '/kaggle/working/miniimagenet/'

categories = os.listdir(train_path)
len(categories)

64

In [5]:
for category in categories:
    category_path = os.path.join(train_path, category)
    images = os.listdir(category_path)

    train, rest = train_test_split(images, test_size=0.2, random_state=0)
    val, test = train_test_split(rest, test_size=0.5, random_state=0)

    os.makedirs(os.path.join(output_path, 'train', category), exist_ok=True)
    os.makedirs(os.path.join(output_path, 'val', category), exist_ok=True)
    os.makedirs(os.path.join(output_path, 'test', category), exist_ok=True)
    
    with tqdm(train, desc=f'Copying {category} images to train set') as pbar_train:
        for img in pbar_train:
            shutil.copy(os.path.join(category_path, img), os.path.join(output_path, 'train', category, img))
    with tqdm(val, desc=f'Copying {category} images to validation set') as pbar_val:
        for img in pbar_val:
            shutil.copy(os.path.join(category_path, img), os.path.join(output_path, 'val', category, img))
    with tqdm(test, desc=f'Copying {category} images to test set') as pbar_test:
        for img in pbar_test:
            shutil.copy(os.path.join(category_path, img), os.path.join(output_path, 'test', category, img))

Copying n04435653 images to test set: 100%|██████████| 60/60 [00:00<00:00, 171.50it/s]


In [ ]:
# checkpoint = ModelCheckpoint(filepath='../working/model.weights.best.hdf5',
#                         monitor='val_categorical_accuracy',
#                         save_best_only=True,
#                         verbose=1)

# early_stop = EarlyStopping(monitor='val_categorical_accuracy',
#                            patience=10,
#                            restore_best_weights=True,
#                            mode='max')

In [6]:
# NUM_CLASSES = len(categories)

In [92]:
from torchvision.datasets import ImageFolder

BATCH_SIZE = 32 
# NUM_EPOCHS = 10
# LEARNING_RATE = 1e-3
criterion = nn.CrossEntropyLoss()

train_path = '/kaggle/working/miniimagenet/train/'
val_path = '/kaggle/working/miniimagenet/val/'
test_path = '/kaggle/working/miniimagenet/test/'

transform = transforms.Compose([
#     transforms.RandomResizedCrop(224),
#     transforms.RandomHorizontalFlip(),
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

train_dataset = ImageFolder(train_path, transform=transform)
val_dataset = ImageFolder(val_path, transform=transform)
test_dataset = ImageFolder(test_path, transform=transform)

train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=BATCH_SIZE, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False)

In [8]:
# len(train_dataset.classes)

In [9]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using {device} device")

Using cuda device


In [10]:
from torch.nn.utils import clip_grad_norm_
from torch.optim.lr_scheduler import ReduceLROnPlateau

In [11]:
def train_model(model, train_loader, val_loader, optimizer, criterion, num_epochs=NUM_EPOCHS, early_stopping_patience=3):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    if torch.cuda.device_count() > 1:
        print(f"{torch.cuda.device_count()} GPUs!")
        model = nn.DataParallel(model)
    model.to(device)
    
    train_losses = []
    train_accuracies = []
    val_losses = []
    val_accuracies = []
    
    early_stopping_counter = 0
    best_val_loss = float('inf')
    
    scheduler = ReduceLROnPlateau(optimizer, mode='min', patience=2, verbose=True)
    
    for epoch in range(num_epochs):
        model.train()
        train_progress_bar = tqdm(train_loader, desc=f'Epoch {epoch+1}/{num_epochs} [Training]')
        running_loss = 0.0
        correct = 0
        total = 0
        
        for inputs, labels in train_progress_bar:
            inputs, labels = inputs.to(device), labels.to(device)
            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            
            running_loss += loss.item()

            _, predicted = outputs.max(1)
            total += labels.size(0)
            correct += predicted.eq(labels).sum().item()

            train_progress_bar.set_postfix(loss=loss.item())
            
        train_accuracy = correct / total
        average_loss = running_loss / len(train_loader)
        
        train_losses.append(average_loss)
        train_accuracies.append(train_accuracy)

        model.eval()
        val_loss = 0.0
        correct = 0
        total = 0
        val_progress_bar = tqdm(val_loader, desc=f'Epoch {epoch+1}/{num_epochs} [Validation]')
        
        with torch.no_grad():
            for inputs, labels in val_progress_bar:
                inputs, labels = inputs.to(device), labels.to(device)
                outputs = model(inputs)
                loss = criterion(outputs, labels)
                val_loss += loss.item()
                _, predicted = outputs.max(1)
                total += labels.size(0)
                correct += predicted.eq(labels).sum().item()
                
                val_progress_bar.set_postfix(loss=loss.item())

            val_accuracy = correct / total
            avg_val_loss = val_loss/len(val_loader)
            
            scheduler.step(avg_val_loss)
        
            val_losses.append(avg_val_loss)
            val_accuracies.append(val_accuracy)
            
            print(f'Epoch {epoch+1}/{num_epochs}, Training Loss: {average_loss:.4f}, Training Accuracy: {train_accuracy:.4f}, Validation Loss: {:.4f}, Validation Accuracy: {val_accuracy:.4f}')
            
            if avg_val_loss < best_val_loss:
                best_val_loss = avg_val_loss
                early_stopping_counter = 0
            else:
                early_stopping_counter += 1

            if early_stopping_counter >= early_stopping_patience:
                print(f"Early stopping after {epoch + 1} epochs without improvement in validation loss.")
                break
            
    return train_losses, train_accuracies, val_losses, val_accuracies

In [12]:
def test_model(model, test_loader, criterion):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    if torch.cuda.device_count() > 1:
        print(f"{torch.cuda.device_count()} GPUs!")
        model = nn.DataParallel(model)
    model = model.to(device)
    model.eval()

    correct = 0
    total = 0
    test_loss = 0
    test_progress_bar = tqdm(test_loader, desc='Testing')
    
    with torch.no_grad():
        for inputs, labels in test_progress_bar:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            test_loss += loss.item()
            _, predicted = outputs.max(1)
            total += labels.size(0)
            correct += predicted.eq(labels).sum().item()

            batch_accuracy = predicted.eq(labels).sum().item() / labels.size(0)
            test_progress_bar.set_postfix(batch_accuracy=f'{batch_accuracy:.4f}')
    
    avg_loss = test_loss / len(test_loader)
    test_accuracy = correct / total
    print(f'Test Loss: {avg_loss:.4f}, Test Accuracy: {test_accuracy:.4f}')
    return avg_loss, test_accuracy

In [13]:
torch.cuda.empty_cache()

### ResNet18 with pretrained True

In [22]:
class ResNet18(nn.Module):
    def __init__(self, NUM_CLASSES):
        super(ResNet18, self).__init__()
        self.resnet18 = models.resnet18(pretrained=True)
        for param in self.resnet18.parameters():
            param.requires_grad = False
        in_features = self.resnet18.fc.in_features
        self.resnet18.fc = nn.Linear(in_features, NUM_CLASSES)

    def forward(self, x):
        return self.resnet18(x)

In [ ]:
# def objective(trial):
#     num_classes = len(train_dataset.classes)
#     model = ResNet18(num_classes)
#     lr = trial.suggest_loguniform('lr', 1e-5, 1e-1)
#     optimizer_name = trial.suggest_categorical('optimizer', ['Adam', 'SGD', 'RMSprop', 'AdamW'])
#     optimizer = getattr(optim, optimizer_name)(model.parameters(), lr=lr)
#     criterion = nn.CrossEntropyLoss()
    
#     return train_model(model, train_loader, val_loader, optimizer, criterion, num_epochs=NUM_EPOCHS)

In [ ]:
# study = optuna.create_study(direction='maximize')
# study.optimize(objective, n_trials=5)

# best_params = study.best_params
# print("Best Hyperparameters:", best_params)

In [ ]:
# best_model = ResNet18(len(train_dataset.classes)).to(device)
# best_optimizer = getattr(optim, best_params['optimizer'])(best_model.parameters(), lr=best_params['lr'])
# best_optimizer

In [27]:
NUM_CLASSES = len(train_dataset.classes)
NUM_EPOCHS = 10
LEARNING_RATE = 0.0001

resnet18_model = ResNet18(NUM_CLASSES).to(device)
optimizer = optim.AdamW(resnet18_model.parameters(), lr=LEARNING_RATE, weight_decay=0.1)
criterion = nn.CrossEntropyLoss()

train_model(resnet18_model, train_loader, val_loader, optimizer, criterion, num_epochs=NUM_EPOCHS)

2 GPUs!


Epoch 1/10 [Validation]: 100%|██████████| 120/120 [00:10<00:00, 11.65it/s, loss=2.96]


Epoch 1/10, Training Loss: 3.1844, Training Accuracy: 0.3590, Validation Loss: 2.1652, Validation Accuracy: 0.6346


Epoch 2/10 [Validation]: 100%|██████████| 120/120 [00:10<00:00, 11.69it/s, loss=1.99] 


Epoch 2/10, Training Loss: 1.9578, Training Accuracy: 0.6596, Validation Loss: 1.4524, Validation Accuracy: 0.7190


...

Epoch 9/10 [Validation]: 100%|██████████| 120/120 [00:10<00:00, 11.83it/s, loss=1.2]  


Epoch 9/10, Training Loss: 0.8984, Training Accuracy: 0.7738, Validation Loss: 0.8118, Validation Accuracy: 0.7826


Epoch 10/10 [Validation]: 100%|██████████| 120/120 [00:10<00:00, 11.77it/s, loss=1.08] 

Epoch 10/10, Training Loss: 0.8701, Training Accuracy: 0.7783, Validation Loss: 0.7701, Validation Accuracy: 0.7875


0.7875

In [28]:
torch.save(resnet18_model.state_dict(), 'ResNet18_model.pth')

In [ ]:
epochs = range(1, len(train_losses) + 1)

# Training vs Validation Loss
plt.figure(figsize=(12, 4))
plt.subplot(1, 2, 1)
plt.plot(epochs, train_losses, label='Training Loss')
plt.plot(epochs, val_losses, label='Validation Loss')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.title('Training vs Validation Loss')
plt.legend()

# Training vs Validation Accuracy
plt.subplot(1, 2, 2)
plt.plot(epochs, train_accuracies, label='Training Accuracy')
plt.plot(epochs, val_accuracies, label='Validation Accuracy')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.title('Training vs Validation Accuracy')
plt.legend()

plt.tight_layout()
plt.show()

In [29]:
model_path = '/kaggle/working/ResNet18_model.pth'
resnet18_model.load_state_dict(torch.load(model_path))
test_model(resnet18_model, test_loader, criterion)

2 GPUs!


Testing: 100%|██████████| 120/120 [00:10<00:00, 11.75it/s, batch_accuracy=0.5312]

Test Loss: 0.8122, Test Accuracy: 0.7766


(0.8122171103333433, 0.7765625)

### VGG16 with pretrained True

In [30]:
class VGG16(nn.Module):
    def __init__(self, NUM_CLASSES):
        super(VGG16, self).__init__()
        self.vgg16 = vgg16(pretrained=True)
        in_features = self.vgg16.classifier[6].in_features
        self.vgg16.classifier[6] = nn.Linear(in_features, NUM_CLASSES)

    def forward(self, x):
        return self.vgg16(x)

In [ ]:
# def objective(trial):
#     num_classes = len(train_dataset.classes)
#     model = VGG16(num_classes)
#     lr = trial.suggest_loguniform('lr', 1e-5, 1e-1)
#     optimizer_name = trial.suggest_categorical('optimizer', ['Adam', 'SGD', 'AdamW', 'RMSprop'])
#     optimizer = getattr(optim, optimizer_name)(model.parameters(), lr=lr)
#     criterion = nn.CrossEntropyLoss()
    
#     val_accuracy = train_model(model, train_loader, val_loader, optimizer, criterion, num_epochs=NUM_EPOCHS)
#     return val_accuracy

In [ ]:
# study = optuna.create_study(direction='maximize')
# study.optimize(objective, n_trials=5)

In [ ]:
# best_params = study.best_params
# print("Best Hyperparameters:", best_params)

In [ ]:
best_model = VGG16(len(train_dataset.classes)).to(device)
best_optimizer = getattr(optim, best_params['optimizer'])(best_model.parameters(), lr=best_params['lr'])
best_optimizer

In [15]:
NUM_CLASSES = len(train_dataset.classes)
NUM_EPOCHS = 10
LEARNING_RATE = 0.0001

model = VGG16(NUM_CLASSES).to(device)
optimizer = optim.RMSprop(model.parameters(), lr=LEARNING_RATE)
criterion = nn.CrossEntropyLoss()

train_model(model, train_loader, val_loader, optimizer, criterion, num_epochs=NUM_EPOCHS)

Downloading: "https://download.pytorch.org/models/vgg16-397923af.pth" to /root/.cache/torch/hub/checkpoints/vgg16-397923af.pth
100%|██████████| 528M/528M [00:02<00:00, 254MB/s]  


2 GPUs!


Epoch 1/10 [Validation]: 100%|██████████| 120/120 [00:23<00:00,  5.08it/s, loss=3.54]


Epoch 1/10, Training Loss: 3.7198, Training Accuracy: 0.0852, Validation Loss: 3.0852, Validation Accuracy: 0.1865


Epoch 2/10 [Validation]: 100%|██████████| 120/120 [00:23<00:00,  5.07it/s, loss=3.72] 


...

Epoch 9/10 [Validation]: 100%|██████████| 120/120 [00:24<00:00,  4.91it/s, loss=1.09] 


Epoch 9/10, Training Loss: 1.4329, Training Accuracy: 0.6222, Validation Loss: 1.6098, Validation Accuracy: 0.5784


Epoch 10/10 [Validation]: 100%|██████████| 120/120 [00:24<00:00,  4.89it/s, loss=1.41] 

Epoch 10/10, Training Loss: 1.3889, Training Accuracy: 0.6337, Validation Loss: 1.5487, Validation Accuracy: 0.6049


0.6049479166666667

In [20]:
torch.save(model.state_dict(), 'VGG16_model.pth')

In [ ]:
epochs = range(1, len(train_losses) + 1)

# Training vs Validation Loss
plt.figure(figsize=(12, 4))
plt.subplot(1, 2, 1)
plt.plot(epochs, train_losses, label='Training Loss')
plt.plot(epochs, val_losses, label='Validation Loss')
plt.xlabel('Epochs')
plt.ylabel('Loss')
plt.title('Training vs Validation Loss')
plt.legend()

# Training vs Validation Accuracy
plt.subplot(1, 2, 2)
plt.plot(epochs, train_accuracies, label='Training Accuracy')
plt.plot(epochs, val_accuracies, label='Validation Accuracy')
plt.xlabel('Epochs')
plt.ylabel('Accuracy')
plt.title('Training vs Validation Accuracy')
plt.legend()

plt.tight_layout()
plt.show()

In [21]:
model_path = '/kaggle/working/VGG16_model.pth'
model.load_state_dict(torch.load(model_path))
test_model(model, test_loader, criterion)

2 GPUs!


Testing: 100%|██████████| 120/120 [00:23<00:00,  5.00it/s, batch_accuracy=0.7188]

Test Loss: 1.5689, Test Accuracy: 0.5948


(1.568903627122442, 0.5947916666666667)